##  1. Download and Explore Dataset

In [1]:
!pip install bs4
#!pip install plotly

import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library



print('Libraries imported.')

     |████████████████████████████████| 122kB 30.5MB/s eta 0:00:01
  Stored in directory: /home/jupyterlab/.cache/pip/wheels/a0/b0/b2/4f80b9456b87abedbc0bf2d52235414c3467d8889be38dd472
Successfully built bs4
Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geographiclib-1.52         |     pyhd8ed1ab_0          35 KB  conda-forge
    geopy-2.2.0                |     pyhd8ed1ab_0          67 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         102 KB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.52-pyhd8ed1ab_0
  geopy              conda-forge/noarch::geopy-2.2.0-pyhd8ed1ab_0



geographiclib-1.52   | 35 

In [2]:
cdmx_data=pd.read_csv("CMXcoords.csv")
cdmx_data.head()

PostalCode         Borough Type of Neighborhood         Neighborhood  \
0        1857  Álvaro Obregón              Colonia  Lomas de Chamontoya   
1        1859  Álvaro Obregón              Colonia           Tlacoyaque   
2        1860  Álvaro Obregón              Colonia      Lomas de La Era   
3        1863  Álvaro Obregón              Colonia    Lomas del Capulín   
4        1870  Álvaro Obregón              Colonia  Lomas de los Cedros   

   Latitude  Longitude  
0  19.32585  -99.25724  
1  19.31489  -99.27014  
2  19.32225  -99.26505  
3  19.31747  -99.26494  
4  19.30533  -99.27068

In [3]:
 cdmx_data['PostalCode'].describe()

count     1515.000000
mean      8543.928053
std       4909.859519
min       1000.000000
25%       4260.000000
50%       8910.000000
75%      13099.500000
max      16900.000000
Name: PostalCode, dtype: float64

### Data Wrangling

In [4]:
 cdmx_data.shape

(1515, 6)

In [5]:
# look for NAN values
cdmx_data.isnull().values.any()


False

In [6]:
cdmx_data.describe(include="all")


PostalCode         Borough Type of Neighborhood Neighborhood  \
count    1515.000000            1515                 1515         1515   
unique           NaN              16                    6         1367   
top              NaN  Álvaro Obregón              Colonia   San Miguel   
freq             NaN             222                 1255            8   
mean     8543.928053             NaN                  NaN          NaN   
std      4909.859519             NaN                  NaN          NaN   
min      1000.000000             NaN                  NaN          NaN   
25%      4260.000000             NaN                  NaN          NaN   
50%      8910.000000             NaN                  NaN          NaN   
75%     13099.500000             NaN                  NaN          NaN   
max     16900.000000             NaN                  NaN          NaN   

           Latitude    Longitude  
count   1515.000000  1515.000000  
unique          NaN          NaN  
top             NaN          NaN  
freq            NaN          NaN  
mean      19.376632   -99.150321  
std        0.355640     0.500013  
min       16.286210  -116.635340  
25%       19.306595   -99.200615  
50%       19.364240   -99.143810  
75%       19.441475   -99.101855  
max       31.890930   -93.096720

In [7]:
#Drop specific duplicate and specific columns and then create a new data frame 
cdmx_data=cdmx_data.drop(['Type of Neighborhood'], axis=1)

In [8]:
cdmx_data.drop_duplicates
cdmx_data.head()

PostalCode         Borough         Neighborhood  Latitude  Longitude
0        1857  Álvaro Obregón  Lomas de Chamontoya  19.32585  -99.25724
1        1859  Álvaro Obregón           Tlacoyaque  19.31489  -99.27014
2        1860  Álvaro Obregón      Lomas de La Era  19.32225  -99.26505
3        1863  Álvaro Obregón    Lomas del Capulín  19.31747  -99.26494
4        1870  Álvaro Obregón  Lomas de los Cedros  19.30533  -99.27068

### Use geopy library to get the latitude and longitude values of Mexico City.¶

In [9]:
address = 'CDMX,MX'

geolocator = Nominatim(user_agent="mx_cdmx")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of MExico City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of MExico City are 19.4326296, -99.1331785.


In [10]:
cdmx_data.describe(include="all")

PostalCode         Borough Neighborhood     Latitude    Longitude
count    1515.000000            1515         1515  1515.000000  1515.000000
unique           NaN              16         1367          NaN          NaN
top              NaN  Álvaro Obregón   San Miguel          NaN          NaN
freq             NaN             222            8          NaN          NaN
mean     8543.928053             NaN          NaN    19.376632   -99.150321
std      4909.859519             NaN          NaN     0.355640     0.500013
min      1000.000000             NaN          NaN    16.286210  -116.635340
25%      4260.000000             NaN          NaN    19.306595   -99.200615
50%      8910.000000             NaN          NaN    19.364240   -99.143810
75%     13099.500000             NaN          NaN    19.441475   -99.101855
max     16900.000000             NaN          NaN    31.890930   -93.096720

In [11]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len( cdmx_data['Borough'].unique()),
         cdmx_data.shape[0]
    )
)

The dataframe has 16 boroughs and 1515 neighborhoods.


### Create a copy of cdmx_data and call it neighborhoods

In [12]:


neighborhoods=cdmx_data.copy(deep= True)
neighborhoods.head()

PostalCode         Borough         Neighborhood  Latitude  Longitude
0        1857  Álvaro Obregón  Lomas de Chamontoya  19.32585  -99.25724
1        1859  Álvaro Obregón           Tlacoyaque  19.31489  -99.27014
2        1860  Álvaro Obregón      Lomas de La Era  19.32225  -99.26505
3        1863  Álvaro Obregón    Lomas del Capulín  19.31747  -99.26494
4        1870  Álvaro Obregón  Lomas de los Cedros  19.30533  -99.27068

### Create a map of Mexico City with neighborhoods superimposed on top.¶

In [13]:
# create map of Toronto using latitude and longitude values
map_cdmx = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip( neighborhoods['Latitude'], neighborhoods['Longitude'],  neighborhoods['Borough'],  neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_cdmx)  
    
map_cdmx

In [14]:
# Create a slice from  MIguel Hidalgo Borough

In [15]:
miguelh_data = neighborhoods[neighborhoods['Borough'] == 'Miguel Hidalgo'].reset_index(drop=True)
miguelh_data.head()

PostalCode         Borough                       Neighborhood   Latitude  \
0       11000  Miguel Hidalgo     Lomas de Chapultepec I Sección  19.362160   
1       11000  Miguel Hidalgo  Lomas de Chapultepec VIII Sección  19.304240   
2       11000  Miguel Hidalgo    Lomas de Chapultepec II Sección  19.297530   
3       11000  Miguel Hidalgo   Lomas de Chapultepec III Sección  19.267040   
4       11000  Miguel Hidalgo    Lomas de Chapultepec IV Sección  19.216832   

   Longitude  
0 -99.273440  
1 -99.232490  
2 -99.242710  
3 -99.002880  
4 -99.102057

In [16]:
miguelh_data.describe(include="all")

PostalCode         Borough Neighborhood   Latitude   Longitude
count      85.000000              85           85  85.000000   85.000000
unique           NaN               1           85        NaN         NaN
top              NaN  Miguel Hidalgo      América        NaN         NaN
freq             NaN              85            1        NaN         NaN
mean    11438.776471             NaN          NaN  19.426815  -99.147670
std       253.502530             NaN          NaN   0.457762    0.580066
min     11000.000000             NaN          NaN  16.286210 -101.011620
25%     11280.000000             NaN          NaN  19.416830  -99.203120
50%     11450.000000             NaN          NaN  19.444490  -99.193210
75%     11560.000000             NaN          NaN  19.453230  -99.173650
max     11950.000000             NaN          NaN  22.151420  -94.191610

In [17]:
address = 'Miguel Hidalgo,CDMX'

geolocator = Nominatim(user_agent="MHidalgo")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Miguel Hidalgo Borough are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Miguel Hidalgo Borough are 19.4075059, -99.1917103.


In [18]:
# create map of MIguel Hidalgo borough using latitude and longitude values
map_mhidalgo = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(miguelh_data['Latitude'], miguelh_data['Longitude'], miguelh_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='orange',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_mhidalgo)  
    
map_mhidalgo

## Define Foursquare Credentials and Version

In [19]:
CLIENT_ID = 'JRWH0X0QSE5RUZSK2XMC5ZJWHOBIN51ITQJ2CD4NZMAGN0Z3' # your Foursquare ID
CLIENT_SECRET = 'LBQZKN1PEPN5MWGFSFKTUB24PP2I3BQJ3I3PU5YEHQREJBVP' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: JRWH0X0QSE5RUZSK2XMC5ZJWHOBIN51ITQJ2CD4NZMAGN0Z3
CLIENT_SECRET:LBQZKN1PEPN5MWGFSFKTUB24PP2I3BQJ3I3PU5YEHQREJBVP


### Let's explore the first neighborhood in our dataframe.¶

In [20]:
miguelh_data.loc[0, 'Neighborhood']

'Lomas de Chapultepec I Sección'

#### Get the neighborhood's latitude and longitude values.

In [21]:
neighborhood_latitude =  miguelh_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = miguelh_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name =  miguelh_data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Lomas de Chapultepec I Sección are 19.362160000000074, -99.27343999999994.


#### Now, let's get the top 100 venues that are in Chapultepec Seccion I within a radius of 500 meters.
First, let's create the GET request URL. Name your URL url.

In [22]:
LIMIT=100 
radius=500

url= 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL





'https://api.foursquare.com/v2/venues/explore?&client_id=JRWH0X0QSE5RUZSK2XMC5ZJWHOBIN51ITQJ2CD4NZMAGN0Z3&client_secret=LBQZKN1PEPN5MWGFSFKTUB24PP2I3BQJ3I3PU5YEHQREJBVP&v=20180605&ll=19.362160000000074,-99.27343999999994&radius=500&limit=100'

In [23]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '60ff67b99372fd723fa8f6bf'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Cuajimalpa',
  'headerFullLocation': 'Cuajimalpa',
  'headerLocationGranularity': 'city',
  'totalResults': 68,
  'suggestedBounds': {'ne': {'lat': 19.36666000450008,
    'lng': -99.26867913147505},
   'sw': {'lat': 19.357659995500068, 'lng': -99.27820086852482}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '5a6a81541ffe9765dd0edca2',
       'name': 'Lego Store México',
       'location': {'address': 'Av. Vasco de Quiroga',
        'lat': 19.36174178035355,
        'lng': -99.27279367073803,
        'labeledLatLngs': [{'label': 'display',
          'lat': 19.361741780

In [24]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

### Now we are ready to clean the json and structure it into a pandas dataframe.

In [25]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name          categories        lat        lng
0             Lego Store México    Toy / Game Store  19.361742 -99.272794
1  Mexicano (Liverpool Gourmet)  Mexican Restaurant  19.361587 -99.274490
2               Centro Santa Fe       Shopping Mall  19.361314 -99.273878
3                     Liverpool    Department Store  19.361531 -99.274371
4           Distroller Santa Fé    Toy / Game Store  19.361183 -99.273713

In [26]:
nearby_venues.describe()

lat        lng
count  68.000000  68.000000
mean   19.361037 -99.273999
std     0.001193   0.001946
min    19.357926 -99.277504
25%    19.360608 -99.275522
50%    19.361128 -99.274430
75%    19.361626 -99.272370
max    19.363343 -99.269942

In [27]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

68 venues were returned by Foursquare.


## 2. Explore Neighborhoods in Miguel Hidalgo Borough

#### Let's create a function to repeat the same process to all the neighborhoods in Miguel Hidalgo¶

In [28]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [29]:

miguelh_venues= getNearbyVenues(names=miguelh_data['Neighborhood'],
                                   latitudes=miguelh_data['Latitude'],
                                   longitudes=miguelh_data['Longitude']
                                  )

Lomas de Chapultepec I Sección
Lomas de Chapultepec VIII Sección
Lomas de Chapultepec II Sección
Lomas de Chapultepec III Sección
Lomas de Chapultepec IV Sección
Lomas de Chapultepec V Sección
Lomas de Chapultepec VI Sección
Lomas de Chapultepec VII Sección
Molino del Rey
Bosque de Chapultepec II Sección
Bosque de Chapultepec III Sección
Lomas Hermosa
Lomas de Sotelo
San Lorenzo Tlaltenango
Periodista
Argentina Poniente
Ignacio Manuel Altamirano
10 de Abril
México Nuevo
San Joaquín
Bosque de las Lomas
Escandón I Sección
Escandón II Sección
16 de Septiembre
América
Daniel Garza
Ampliación Daniel Garza
San Miguel Chapultepec I Sección
San Miguel Chapultepec II Sección
Observatorio
Tacubaya
Lomas de Bezares
Real de las Lomas
Lomas de Reforma
Lomas Altas
Argentina Antigua
Torre Blanca
Ampliación Torre Blanca
Huíchapan
San Diego Ocoyoacac
Verónica Anzures
Mariano Escobedo
Anáhuac I Sección
Anáhuac II Sección
Un Hogar Para Nosotros
Santo Tomas
Plutarco Elías Calles
Agricultura
Tlaxpana
Popot

In [30]:
print(miguelh_venues.shape)
miguelh_venues.head()

(2933, 7)


Neighborhood  Neighborhood Latitude  \
0  Lomas de Chapultepec I Sección               19.36216   
1  Lomas de Chapultepec I Sección               19.36216   
2  Lomas de Chapultepec I Sección               19.36216   
3  Lomas de Chapultepec I Sección               19.36216   
4  Lomas de Chapultepec I Sección               19.36216   

   Neighborhood Longitude                         Venue  Venue Latitude  \
0               -99.27344             Lego Store México       19.361742   
1               -99.27344  Mexicano (Liverpool Gourmet)       19.361587   
2               -99.27344               Centro Santa Fe       19.361314   
3               -99.27344                     Liverpool       19.361531   
4               -99.27344           Distroller Santa Fé       19.361183   

   Venue Longitude      Venue Category  
0       -99.272794    Toy / Game Store  
1       -99.274490  Mexican Restaurant  
2       -99.273878       Shopping Mall  
3       -99.274371    Department Store  
4       -99.273713    Toy / Game Store

In [31]:
miguelh_venues.describe(include="all")

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
count              2933            2933.000000             2933.000000   
unique               85                    NaN                     NaN   
top     Campo Militar 1                    NaN                     NaN   
freq                100                    NaN                     NaN   
mean                NaN              19.499374              -99.233923   
std                 NaN               0.444773                0.321149   
min                 NaN              16.286210             -101.011620   
25%                 NaN              19.426170              -99.203310   
50%                 NaN              19.441140              -99.194650   
75%                 NaN              19.447030              -99.177390   
max                 NaN              22.151420              -94.191610   

            Venue  Venue Latitude  Venue Longitude      Venue Category  
count        2933     2933.000000      2933.000000                2933  
unique       1672             NaN              NaN                 249  
top     Starbucks             NaN              NaN  Mexican Restaurant  
freq           62             NaN              NaN                 273  
mean          NaN       19.499260       -99.234165                 NaN  
std           NaN        0.444573         0.321134                 NaN  
min           NaN       16.287476      -101.016197                 NaN  
25%           NaN       19.426988       -99.203781                 NaN  
50%           NaN       19.438995       -99.196232                 NaN  
75%           NaN       19.447950       -99.178940                 NaN  
max           NaN       22.154715       -94.194803                 NaN

### Let's check how many venues were returned for each neighborhood

In [32]:
miguelh_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                               
10 de Abril                                           46   
16 de Septiembre                                       4   
5 de Mayo                                             27   
Agricultura                                           33   
Ahuehuetes Anáhuac                                    35   
Ampliación Daniel Garza                               18   
Ampliación Granada                                    27   
Ampliación Popo                                       27   
Ampliación Torre Blanca                              100   
América                                                3   
Anzures                                               85   
Anáhuac I Sección                                     23   
Anáhuac II Sección                                    48   
Argentina Antigua                                     14   
Argentina Poniente                                    28   
Bosque de Chapultepec I Sección                       56   
Bosque de Chapultepec II Sección                       4   
Bosque de Chapultepec III Sección                     56   
Bosque de las Lomas                                    4   
Campo Militar 1                                      100   
Cuauhtémoc Pensil                                     25   
Daniel Garza                                           4   
Deportivo Pensil                                      22   
Dos Lagos                                             28   
Escandón I Sección                                     4   
Escandón II Sección                                    5   
Francisco I Madero                                    48   
Granada                                               46   
Huíchapan                                             88   
Ignacio Manuel Altamirano                              4   
Irrigación                                            51   
Lago Norte                                            12   
Lago Sur                                              29   
Legaria                                               27   
Lomas Altas                                            8   
Lomas Hermosa                                         56   
Lomas de Bezares                                      35   
Lomas de Chapultepec I Sección                        68   
Lomas de Chapultepec II Sección                        7   
Lomas de Chapultepec III Sección                      21   
Lomas de Chapultepec IV Sección                        6   
Lomas de Chapultepec V Sección                         4   
Lomas de Chapultepec VI Sección                       56   
Lomas de Chapultepec VII Sección                      56   
Lomas de Chapultepec VIII Sección                     18   
Lomas de Reforma                                      38   
Lomas de Sotelo                                       56   
Los Manzanos                                          27   
Manuel Avila Camacho                                   2   
Mariano Escobedo                                      34   
Modelo Pensil                                         31   
Molino del Rey                                        28   
México Nuevo                                          31   
Nextitla                                              35   
Observatorio                                          13   
Pensil Norte                                          20   
Pensil Sur                                            24   
Peralitos                                             21   
Periodista                                            30   
Plutarco Elías Calles                                 35   
Polanco I Sección                                     40   
Polanco II Sección                                    28   
Polanco III Sección                                   20   
Polanco IV Sección                                    72   
Polanco V Sección                                     86   
Popo           

In [33]:
miguelh_venues.describe(include="all")

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
count              2933            2933.000000             2933.000000   
unique               85                    NaN                     NaN   
top     Campo Militar 1                    NaN                     NaN   
freq                100                    NaN                     NaN   
mean                NaN              19.499374              -99.233923   
std                 NaN               0.444773                0.321149   
min                 NaN              16.286210             -101.011620   
25%                 NaN              19.426170              -99.203310   
50%                 NaN              19.441140              -99.194650   
75%                 NaN              19.447030              -99.177390   
max                 NaN              22.151420              -94.191610   

            Venue  Venue Latitude  Venue Longitude      Venue Category  
count        2933     2933.000000      2933.000000                2933  
unique       1672             NaN              NaN                 249  
top     Starbucks             NaN              NaN  Mexican Restaurant  
freq           62             NaN              NaN                 273  
mean          NaN       19.499260       -99.234165                 NaN  
std           NaN        0.444573         0.321134                 NaN  
min           NaN       16.287476      -101.016197                 NaN  
25%           NaN       19.426988       -99.203781                 NaN  
50%           NaN       19.438995       -99.196232                 NaN  
75%           NaN       19.447950       -99.178940                 NaN  
max           NaN       22.154715       -94.194803                 NaN

### Let's find out how many unique categories can be curated from all the returned venues

In [34]:
print('There are {} uniques categories.'.format(len(miguelh_venues['Venue Category'].unique())))

There are 249 uniques categories.


## 3. Analyze Each Neighborhood

In [35]:
# one hot encoding
miguelh_onehot = pd.get_dummies(miguelh_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
miguelh_onehot['Neighborhood'] = miguelh_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [miguelh_onehot.columns[-1]] + list(miguelh_onehot.columns[:-1])
miguelh_onehot = miguelh_onehot[fixed_columns]
miguelh_onehot.head()

Neighborhood  Accessories Store  African Restaurant  \
0  Lomas de Chapultepec I Sección                  0                   0   
1  Lomas de Chapultepec I Sección                  0                   0   
2  Lomas de Chapultepec I Sección                  0                   0   
3  Lomas de Chapultepec I Sección                  0                   0   
4  Lomas de Chapultepec I Sección                  0                   0   

   American Restaurant  Antique Shop  Arepa Restaurant  \
0                    0             0                 0   
1                    0             0                 0   
2                    0             0                 0   
3                    0             0                 0   
4                    0             0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Garage  BBQ Joint  Bagel Shop  \
0                 0                   0            0          0           0   
1                 0                   0            0          0           0   
2                 0                   0            0          0           0   
3                 0                   0            0          0           0   
4                 0                   0            0          0           0   

   Bakery  Bank  Bar  Baseball Field  Basketball Stadium  Bed & Breakfast  \
0       0     0    0               0                   0                0   
1       0     0    0               0                   0                0   
2       0     0    0               0                   0                0   
3       0     0    0               0                   0                0   
4       0     0    0               0                   0                0   

   Beer Bar  Beer Garden  Belgian Restaurant  Bike Rental / Bike Share  \
0         0            0                   0                         0   
1         0            0                   0                         0   
2         0            0                   0                         0   
3         0            0                   0                         0   
4         0            0                   0                         0   

   Bike Trail  Bistro  Bookstore  Boutique  Bowling Alley  \
0           0       0          0         0              0   
1           0       0          0         0              0   
2           0       0          0         0              0   
3           0       0          0         0              0   
4           0       0          0         0              0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Buffet  Building  Burger Joint  Burrito Place  \
0                0       0         0             0              0   
1                0       0         0             0              0   
2                0       0         0             0              0   
3                0       0         0             0              0   
4                0       0         0             0              0   

   Bus Station  Business Service  Cafeteria  Café  Cajun / Creole Restaurant  \
0            0                 0          0     0                          0   
1            0                 0          0     

In [36]:
#And let's examine the new dataframe size.

miguelh_onehot.shape

(2933, 250)

### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [37]:
miguelh_grouped = miguelh_onehot.groupby('Neighborhood').mean().reset_index()
miguelh_grouped

Neighborhood  Accessories Store  African Restaurant  \
0                         10 de Abril           0.000000            0.000000   
1                    16 de Septiembre           0.000000            0.000000   
2                           5 de Mayo           0.000000            0.000000   
3                         Agricultura           0.000000            0.000000   
4                  Ahuehuetes Anáhuac           0.000000            0.000000   
5             Ampliación Daniel Garza           0.000000            0.000000   
6                  Ampliación Granada           0.000000            0.000000   
7                     Ampliación Popo           0.000000            0.000000   
8             Ampliación Torre Blanca           0.000000            0.000000   
9                             América           0.000000            0.000000   
10                            Anzures           0.000000            0.000000   
11                  Anáhuac I Sección           0.000000            0.000000   
12                 Anáhuac II Sección           0.000000            0.000000   
13                  Argentina Antigua           0.000000            0.000000   
14                 Argentina Poniente           0.000000            0.000000   
15    Bosque de Chapultepec I Sección           0.000000            0.000000   
16   Bosque de Chapultepec II Sección           0.000000            0.000000   
17  Bosque de Chapultepec III Sección           0.000000            0.000000   
18                Bosque de las Lomas           0.000000            0.000000   
19                    Campo Militar 1           0.000000            0.000000   
20                  Cuauhtémoc Pensil           0.000000            0.000000   
21                       Daniel Garza           0.000000            0.000000   
22                   Deportivo Pensil           0.000000            0.000000   
23                          Dos Lagos           0.000000            0.000000   
24                 Escandón I Sección           0.000000            0.000000   
25                Escandón II Sección           0.000000            0.000000   
26                 Francisco I Madero           0.000000            0.000000   
27                            Granada           0.000000            0.000000   
28                          Huíchapan           0.000000            0.000000   
29          Ignacio Manuel Altamirano           0.000000            0.000000   
30                         Irrigación           0.000000            0.000000   
31                         Lago Norte           0.000000            0.000000   
32                           Lago Sur           0.000000            0.000000   
33                            Legaria           0.000000            0.037037   
34                        Lomas Altas           0.000000            0.000000   
35                      Lomas Hermosa           0.000000            0.000000   
36                   Lomas de Bezares           0.000000            0.000000   
37     Lomas de Chapultepec I Sección           0.000000            0.000000   
38    Lomas de Chapultepec II Sección           0.000000            0.000000   
39   Lomas de Chapultepec III Sección           0.000000            0.000000   
40    Lomas de Chapultepec IV Sección           0.000000            0.000000   
41     Lomas de Chapultepec V Sección           0.000000            0.000000   
42    Lomas de Chapultepec VI Sección           0.000000            0.000000   
43   Lomas de Chapultepec VII Sección           0.000000            0.000000   
44  Lomas de Chapultepec VIII Sección           0.000000            0.000000   
45                   Lomas de Reforma           0.000000            0.000000   
46                    Lomas de Sotelo           0.000000            0.000000   
47                       Los Manzanos           0.000000            0.000000   
48               Manuel Avila Camacho           0.000000            0.000000   
49                   Mari

In [38]:
# let's check the new size of the DF
miguelh_grouped.shape

(85, 250)

### Let's print each neighborhood along with the top 5 most common venues

In [39]:
num_top_venues = 5

for hood in miguelh_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = miguelh_grouped[miguelh_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----10 de Abril----
                venue  freq
0  Mexican Restaurant  0.15
1   Convenience Store  0.11
2          Taco Place  0.07
3            Pharmacy  0.04
4          Food Truck  0.04


----16 de Septiembre----
                     venue  freq
0           Farmers Market  0.25
1                     Pool  0.25
2                 Mountain  0.25
3  Health & Beauty Service  0.25
4        Accessories Store  0.00


----5 de Mayo----
                venue  freq
0  Mexican Restaurant  0.19
1          Taco Place  0.15
2        Burger Joint  0.07
3                 Gym  0.07
4         Coffee Shop  0.07


----Agricultura----
            venue  freq
0      Restaurant  0.09
1      Food Truck  0.06
2     Coffee Shop  0.06
3  Breakfast Spot  0.06
4  Ice Cream Shop  0.06


----Ahuehuetes Anáhuac----
                venue  freq
0          Taco Place  0.17
1  Mexican Restaurant  0.14
2   Convenience Store  0.09
3         Coffee Shop  0.06
4      Farmers Market  0.06


----Ampliación Daniel Garza----
  

### Let's put that into a pandas dataframe
First, let's write a function to sort the venues in descending order.

In [40]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

#### Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [41]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
miguelh_venues_sorted = pd.DataFrame(columns=columns)
miguelh_venues_sorted['Neighborhood'] = miguelh_grouped['Neighborhood']

for ind in np.arange(miguelh_grouped.shape[0]):
    miguelh_venues_sorted.iloc[ind, 1:] = return_most_common_venues(miguelh_grouped.iloc[ind, :], num_top_venues)

miguelh_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0         10 de Abril    Mexican Restaurant     Convenience Store   
1    16 de Septiembre        Farmers Market              Mountain   
2           5 de Mayo    Mexican Restaurant            Taco Place   
3         Agricultura            Restaurant                   Gym   
4  Ahuehuetes Anáhuac            Taco Place    Mexican Restaurant   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0               Taco Place              Pharmacy            Food Truck   
1  Health & Beauty Service                  Pool    Falafel Restaurant   
2             Burger Joint           Coffee Shop                   Gym   
3           Breakfast Spot           Coffee Shop        Ice Cream Shop   
4        Convenience Store                Bakery        Farmers Market   

         6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                 Burger Joint                  Park            Restaurant   
1  Eastern European Restaurant     Electronics Store           Event Space   
2                   Skate Park                 Diner                  Café   
3                   Food Truck                Bakery    Italian Restaurant   
4                  Coffee Shop                   Bar                 Motel   

  9th Most Common Venue 10th Most Common Venue  
0           Pizza Place             Sports Bar  
1               Exhibit                   Fair  
2            Restaurant     Athletics & Sports  
3     Electronics Store           Liquor Store  
4            Food Truck         Breakfast Spot

In [42]:
miguelh_venues_sorted.describe()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
count                85                    85                    85   
unique               85                    23                    28   
top     Ampliación Popo    Mexican Restaurant    Mexican Restaurant   
freq                  1                    28                    16   

       3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
count                     85                    85                    85   
unique                    39                    42                    40   
top               Taco Place            Taco Place        Ice Cream Shop   
freq                       9                    10                     7   

       6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
count                     85                    85                    85   
unique                    51                    48                    46   
top                   Bakery             Gift Shop              Pharmacy   
freq                      10                     6                     6   

       9th Most Common Venue 10th Most Common Venue  
count                     85                     85  
unique                    48                     50  
top       Mexican Restaurant                    Spa  
freq                       6                      6

## 4. Cluster Neighborhoods¶
Run k-means to cluster the neighborhood into 5 clusters.

In [43]:
# set number of clusters
kclusters = 10

miguelh_grouped_clustering = miguelh_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(miguelh_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 3, 9, 2, 9, 1, 1, 9, 2, 7], dtype=int32)

#### Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [44]:
# add clustering labels
miguelh_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

miguelh_merged = miguelh_data

# merge miguelh_grouped with miguelh_data to add latitude/longitude for each neighborhood

miguelh_merged = miguelh_merged.join(miguelh_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

miguelh_merged.head() # check the last columns!

PostalCode         Borough                       Neighborhood   Latitude  \
0       11000  Miguel Hidalgo     Lomas de Chapultepec I Sección  19.362160   
1       11000  Miguel Hidalgo  Lomas de Chapultepec VIII Sección  19.304240   
2       11000  Miguel Hidalgo    Lomas de Chapultepec II Sección  19.297530   
3       11000  Miguel Hidalgo   Lomas de Chapultepec III Sección  19.267040   
4       11000  Miguel Hidalgo    Lomas de Chapultepec IV Sección  19.216832   

   Longitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0 -99.273440               2           Coffee Shop      Department Store   
1 -99.232490               1            Taco Place  Gym / Fitness Center   
2 -99.242710               1                 Plaza            Playground   
3 -99.002880               1    Mexican Restaurant            Taco Place   
4 -99.102057               0            Taco Place              Mountain   

  3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
0    Mexican Restaurant  Furniture / Home Store            Restaurant   
1    Mexican Restaurant       Convenience Store           Pizza Place   
2        Ice Cream Shop              Taco Place  Gym / Fitness Center   
3    Seafood Restaurant                   Plaza                  Café   
4      Business Service             Beer Garden                Garden   

         6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                     Boutique        Cosmetics Shop     Electronics Store   
1                 Dance Studio      Department Store           Coffee Shop   
2                   Food Truck    Mexican Restaurant           Yoga Studio   
3                     Cemetery                  Fair             BBQ Joint   
4  Eastern European Restaurant           Flea Market     Fish & Chips Shop   

                      9th Most Common Venue       10th Most Common Venue  
0  Residential Building (Apartment / Condo)           Seafood Restaurant  
1                      Other Great Outdoors                  Salad Place  
2                                   Exhibit  Eastern European Restaurant  
3                             Bowling Alley                       Lounge  
4                      Fast Food Restaurant               Farmers Market

### Finally, let's visualize the resulting clusters

In [45]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(miguelh_merged['Latitude'], miguelh_merged['Longitude'], miguelh_merged['Neighborhood'], miguelh_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## 5 examine the clusters

In [46]:
# Cluster 1

miguelh_merged.loc[miguelh_merged['Cluster Labels'] == 0, miguelh_merged.columns[[2] + list(range(5, miguelh_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
4   Lomas de Chapultepec IV Sección               0            Taco Place   
22              Escandón II Sección               0                  Pool   
32                Real de las Lomas               0            Taco Place   
33                 Lomas de Reforma               0            Taco Place   
34                      Lomas Altas               0            Food Truck   
42                Anáhuac I Sección               0            Taco Place   
45                      Santo Tomas               0            Taco Place   
70                       Pensil Sur               0            Taco Place   

      2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
4                  Mountain      Business Service           Beer Garden   
22  Health & Beauty Service            Taco Place              Sake Bar   
32               Food Truck                Museum            Restaurant   
33              Art Gallery            Restaurant           Yoga Studio   
34       Athletics & Sports      Football Stadium             Cafeteria   
42       Mexican Restaurant                   Bar                  Food   
45       Mexican Restaurant     Convenience Store              Creperie   
70        Convenience Store                Bakery           Flea Market   

   5th Most Common Venue        6th Most Common Venue 7th Most Common Venue  \
4                 Garden  Eastern European Restaurant           Flea Market   
22                   Gym                  Yoga Studio           Event Space   
32          Burger Joint           Miscellaneous Shop            Food Court   
33    Mexican Restaurant                       Bakery           Pizza Place   
34            Taco Place                       Market               Brewery   
42               Dog Run                 Burger Joint              Creperie   
45           Pizza Place                    Racetrack        Shipping Store   
70           Pizza Place         Gym / Fitness Center            Food Truck   

   8th Most Common Venue        9th Most Common Venue 10th Most Common Venue  
4      Fish & Chips Shop         Fast Food Restaurant         Farmers Market  
22           Dry Cleaner  Eastern European Restaurant      Electronics Store  
32      Sushi Restaurant                  Salad Place         Sandwich Place  
33        Sandwich Place                  Salad Place                   Park  
34           Wings Joint                Design Studio           Dessert Shop  
42             Multiplex                   Skate Park         Farmers Market  
45           Music Venue                   Skate Park            Flea Market  
70            Food Court                   Restaurant             Donut Shop

In [47]:
# Cluster 2
miguelh_merged.loc[miguelh_merged['Cluster Labels'] == 1, miguelh_merged.columns[[2] + list(range(5, miguelh_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
1   Lomas de Chapultepec VIII Sección               1            Taco Place   
2     Lomas de Chapultepec II Sección               1                 Plaza   
3    Lomas de Chapultepec III Sección               1    Mexican Restaurant   
17                        10 de Abril               1    Mexican Restaurant   
19                        San Joaquín               1    Mexican Restaurant   
21                 Escandón I Sección               1                  Park   
26            Ampliación Daniel Garza               1    Mexican Restaurant   
29                       Observatorio               1    Mexican Restaurant   
35                  Argentina Antigua               1    Mexican Restaurant   
36                       Torre Blanca               1    Mexican Restaurant   
40                   Verónica Anzures               1    Mexican Restaurant   
41                   Mariano Escobedo               1    Mexican Restaurant   
44             Un Hogar Para Nosotros               1    Mexican Restaurant   
61                         Lago Norte               1    Mexican Restaurant   
71                         Irrigación               1    Mexican Restaurant   
72                  Polanco I Sección               1    Mexican Restaurant   
73                            Granada               1    Mexican Restaurant   
74                 Ampliación Granada               1    Mexican Restaurant   
75                 Polanco II Sección               1    Mexican Restaurant   
76                Polanco III Sección               1    Mexican Restaurant   

   2nd Most Common Venue 3rd Most Common Venue  \
1   Gym / Fitness Center    Mexican Restaurant   
2             Playground        Ice Cream Shop   
3             Taco Place    Seafood Restaurant   
17     Convenience Store            Taco Place   
19    Seafood Restaurant          Soccer Field   
21     Convenience Store      Pedestrian Plaza   
26           Coffee Shop            Taco Place   
29           Coffee Shop     Convenience Store   
35        Breakfast Spot    Photography Studio   
36                Bakery            Taco Place   
40                 Hotel            Taco Place   
41            Taco Place              Pharmacy   
44            Taco Place                Lounge   
61            Taco Place          Cupcake Shop   
71            Taco Place          Burger Joint   
72            Restaurant           Coffee Shop   
73            Taco Place            Restaurant   
74                  Park            Taco Place   
75            Steakhouse                  Park   
76            Taco Place    Athletics & Sports   

                       4th Most Common Venue  \
1                          Convenience Store   
2                                 Taco Place   
3                                      Plaza   
17                                  Pharmacy   
19                          Department Store   
21                        Mexican Restaurant   
26                   Health & Beauty Service   
29                       Sporting Goods Shop   
35                                Taco Place   
36                                  Pharmacy   
40                                    Garden   
41                                Restaurant   
44                                      Café   
61                                     Diner   
71                                Restaurant   
72                                Taco Place   
73                               Coffee Shop   
74  Residential Building (Apartment / Condo)   
75                        Athletics & Sports   
76                              Burger Joint   

                       5th Most Common Venue  6th Most Common Venue  \
1                                Pizza Place           Dance Studio   
2                       Gym / Fitness Center             Food Truck   
3                                       Café               Cemetery   
17                   

In [48]:
# Cluster 3
miguelh_merged.loc[miguelh_merged['Cluster Labels'] == 2, miguelh_merged.columns[[2] + list(range(5, miguelh_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
0      Lomas de Chapultepec I Sección               2           Coffee Shop   
6     Lomas de Chapultepec VI Sección               2           Coffee Shop   
7    Lomas de Chapultepec VII Sección               2           Coffee Shop   
8                      Molino del Rey               2    Athletics & Sports   
10  Bosque de Chapultepec III Sección               2           Coffee Shop   
11                      Lomas Hermosa               2           Coffee Shop   
12                    Lomas de Sotelo               2           Coffee Shop   
13            San Lorenzo Tlaltenango               2           Coffee Shop   
14                         Periodista               2    Seafood Restaurant   
15                 Argentina Poniente               2    Athletics & Sports   
18                       México Nuevo               2                Casino   
28  San Miguel Chapultepec II Sección               2          Tennis Court   
37            Ampliación Torre Blanca               2   Arts & Crafts Store   
38                          Huíchapan               2           Coffee Shop   
39                San Diego Ocoyoacac               2           Coffee Shop   
46              Plutarco Elías Calles               2    Mexican Restaurant   
47                        Agricultura               2            Restaurant   
49                            Popotla               2     Convenience Store   
50                            Legaria               2           Coffee Shop   
51                             Tacuba               2            Restaurant   
53                       Pensil Norte               2        Breakfast Spot   
66                 Francisco I Madero               2    Mexican Restaurant   
77                 Polanco IV Sección               2    Mexican Restaurant   
78                  Polanco V Sección               2              Boutique   
79    Bosque de Chapultepec I Sección               2            Restaurant   
80                            Anzures               2    Mexican Restaurant   
83                    Campo Militar 1               2    Mexican Restaurant   
84                     Reforma Social               2              Boutique   

   2nd Most Common Venue 3rd Most Common Venue   4th Most Common Venue  \
0       Department Store    Mexican Restaurant  Furniture / Home Store   
6     Seafood Restaurant                  Café              Taco Place   
7     Seafood Restaurant                  Café              Taco Place   
8                    Gym                Museum        Sculpture Garden   
10    Seafood Restaurant                  Café              Taco Place   
11    Seafood Restaurant                  Café              Taco Place   
12    Seafood Restaurant                  Café              Taco Place   
13    Seafood Restaurant                  Café              Taco Place   
14            Restaurant                Bistro            Cycle Studio   
15                   Gym                Museum        Sculpture Garden   
18    Athletics & Sports      Department Store                  Office   
28           Flea Market                Market             Pizza Place   
37        Clothing Store            Art Museum                  Museum   
38    Mexican Restaurant                 Hotel        Sushi Restaurant   
39            Restaurant        Sandwich Place                     Bar   
46    Seafood Restaurant                   Gym              Taco Place   
47                   Gym        Breakfast Spot             Coffee Shop   
49            Food Truck    Mexican Restaurant              Restaurant   
50            Restaurant           Salad Place      Mexican Restaurant   
51     Convenience Store      Sushi Restaurant        Recording Studio   
53    Mexican Restaurant           Salad Place                  Bakery   
66     Convenience Store          Burger Joint             Coffee Shop   
77           Coffee Shop       

In [49]:
# Cluster 4
miguelh_merged.loc[miguelh_merged['Cluster Labels'] == 3, miguelh_merged.columns[[2] + list(range(5, miguelh_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
23  16 de Septiembre               3        Farmers Market   
25      Daniel Garza               3        Farmers Market   

   2nd Most Common Venue    3rd Most Common Venue 4th Most Common Venue  \
23              Mountain  Health & Beauty Service                  Pool   
25              Mountain  Health & Beauty Service                  Pool   

   5th Most Common Venue        6th Most Common Venue 7th Most Common Venue  \
23    Falafel Restaurant  Eastern European Restaurant     Electronics Store   
25    Falafel Restaurant  Eastern European Restaurant     Electronics Store   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
23           Event Space               Exhibit                   Fair  
25           Event Space               Exhibit                   Fair

In [50]:
# Cluster 5
miguelh_merged.loc[miguelh_merged['Cluster Labels'] == 4, miguelh_merged.columns[[2] + list(range(5, miguelh_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
5  Lomas de Chapultepec V Sección               4                  Farm   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
5              Creperie              Mountain          Cycle Studio   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
5          Dance Studio     Food & Drink Shop                  Food   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
5           Flea Market     Fish & Chips Shop   Fast Food Restaurant

In [51]:
miguelh_merged.loc[miguelh_merged['Cluster Labels'] == 5, miguelh_merged.columns[[2] + list(range(5, miguelh_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
82  Manuel Avila Camacho               5               Stables   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
82                  Park           Yoga Studio      Drive-in Theater   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
82           Flea Market     Fish & Chips Shop  Fast Food Restaurant   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
82        Farmers Market                  Farm     Falafel Restaurant

In [52]:
miguelh_merged.loc[miguelh_merged['Cluster Labels'] == 6, miguelh_merged.columns[[2] + list(range(5, miguelh_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
9   Bosque de Chapultepec II Sección               6          Soccer Field   
16         Ignacio Manuel Altamirano               6          Soccer Field   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
9                 Forest    Seafood Restaurant                Casino   
16                Forest    Seafood Restaurant                Casino   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
9            Yoga Studio      Drive-in Theater  Fast Food Restaurant   
16           Yoga Studio      Drive-in Theater  Fast Food Restaurant   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
9         Farmers Market                  Farm     Falafel Restaurant  
16        Farmers Market                  Farm     Falafel Restaurant

In [53]:
miguelh_merged.loc[miguelh_merged['Cluster Labels'] == 7, miguelh_merged.columns[[2] + list(range(5, miguelh_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
24      América               7           Snack Place         Shopping Mall   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
24              Sake Bar           Yoga Studio      Drive-in Theater   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
24     Fish & Chips Shop  Fast Food Restaurant        Farmers Market   

   9th Most Common Venue 10th Most Common Venue  
24                  Farm     Falafel Restaurant

In [54]:
miguelh_merged.loc[miguelh_merged['Cluster Labels'] == 8, miguelh_merged.columns[[2] + list(range(5, miguelh_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
20  Bosque de las Lomas               8              Mountain   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
20   Housing Development            Food Court                  Park   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
20          Cycle Studio          Dance Studio                  Food   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
20           Flea Market     Fish & Chips Shop   Fast Food Restaurant

In [55]:
miguelh_merged.loc[miguelh_merged['Cluster Labels'] == 9, miguelh_merged.columns[[2] + list(range(5, miguelh_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
27  San Miguel Chapultepec I Sección               9            Taco Place   
30                          Tacubaya               9            Taco Place   
31                  Lomas de Bezares               9            Taco Place   
43                Anáhuac II Sección               9    Mexican Restaurant   
48                          Tlaxpana               9            Restaurant   
52                          Nextitla               9            Taco Place   
54             Ventura Pérez de Alva               9            Taco Place   
55                    Reforma Pensil               9            Taco Place   
56                       San Juanico               9            Taco Place   
57                Ahuehuetes Anáhuac               9            Taco Place   
58                     Modelo Pensil               9            Taco Place   
59                         Peralitos               9    Mexican Restaurant   
60                         Dos Lagos               9          Burger Joint   
62                          Lago Sur               9            Taco Place   
63                      Los Manzanos               9          Burger Joint   
64                         5 de Mayo               9    Mexican Restaurant   
65                  Deportivo Pensil               9            Taco Place   
67                              Popo               9    Mexican Restaurant   
68                   Ampliación Popo               9    Mexican Restaurant   
69                 Cuauhtémoc Pensil               9            Taco Place   
81               Residencial Militar               9    Mexican Restaurant   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
27    Mexican Restaurant            Restaurant                   Bar   
30    Mexican Restaurant           Coffee Shop              Pharmacy   
31    Mexican Restaurant            Food Truck     Convenience Store   
43          Burger Joint            Taco Place            Restaurant   
48            Taco Place          Burger Joint     Convenience Store   
52        Breakfast Spot           Coffee Shop    Mexican Restaurant   
54               Theater    Mexican Restaurant           Coffee Shop   
55    Mexican Restaurant                   Gym     Convenience Store   
56    Mexican Restaurant     Convenience Store                   Bar   
57    Mexican Restaurant     Convenience Store                Bakery   
58    Mexican Restaurant        Breakfast Spot            Restaurant   
59            Taco Place          Burger Joint        Sandwich Place   
60    Mexican Restaurant            Taco Place     Convenience Store   
62    Mexican Restaurant     Convenience Store           Coffee Shop   
63    Mexican Restaurant            Taco Place     Convenience Store   
64            Taco Place          Burger Joint           Coffee Shop   
65    Mexican Restaurant           Coffee Shop     Convenience Store   
67            Taco Place     Convenience Store      Sushi Restaurant   
68          Burger Joint     Convenience Store                   Gym   
69            Restaurant                   Gym    Mexican Restaurant   
81            Taco Place                   Bar          Burger Joint   

            5th Most Common Venue   6th Most Common Venue  \
27                           Café             Snack Place   
30         Furniture / Home Store              Restaurant   
31                   Burger Joint  Furniture / Home Store   
43                            Gym                Pharmacy   
48             Mexican Restaurant              Steakhouse   
52                     Food Truck             Beer Garden   
54                            Bar              Restaurant   
55                       Pharmacy             Wings Joint   
56                    Coffee Shop            Burger Joint   
57                 Farmers Market             Coffee Shop   
58              Convenience Store                  